In [1]:
import pandas as pd
from scipy.stats import spearmanr, pearsonr
from statsmodels.stats.multitest import multipletests

# Пути к файлам
auc_file = r"../../depmap_datasets/prepared_datasets/auc_bosutinib_ctd2.csv"
mapping_file = r"../../depmap_datasets/prepared_datasets/cancer_cell_lines_merged_data.csv"
expression_file = r"../../depmap_datasets/prepared_datasets/protein_coding_gene_expression.csv"
output_folder = r"./correlation_bosutinib_auc_vs_expression"

# Гены для фильтрации
LITERATURE_GENES = [
    "ABL1", "ABL2", "AXL", "BMX", "BTK", "CAMK1D", "CAMK2G", 
    "CAV1", "CSK", "EGFR", "EPHB4", "FER", "FES", "FGR", "FRK", "FYN", 
    "HCK", "LCK", "LYN", "MAP4K2", "MAP4K5", "MINK1", "PTK2", 
    "PTK2B", "SIK1", "SIK2", "SIK3", "SRC", "STK10", "STK24", "STK4", 
    "SYK", "TBK1", "TEC", "TNK2", "YES1"
]

def load_and_prepare_data():
    """Загрузка и подготовка данных с удалением дубликатов DepMap ID"""
    auc_df = pd.read_csv(auc_file)
    mapping_df = pd.read_csv(mapping_file)
    expression_df = pd.read_csv(expression_file)

    # Удаление дубликатов DepMap ID (оставляем строку с минимальным AUC)
    duplicates = auc_df[auc_df.duplicated('ModelID', keep=False)]
    if not duplicates.empty:
        print("Обнаружены дубликаты DepMap ID:")
        
        # Группируем по ModelID и выводим все дубликаты
        for model_id, group in duplicates.groupby('ModelID'):
            print(f"\nДубликаты для ModelID: {model_id}")
            print(group.sort_values('area_under_curve'))
        
        # Оставляем только строки с минимальным AUC для каждого ModelID
        auc_df = auc_df.loc[auc_df.groupby('ModelID')['area_under_curve'].idxmin()]
        
        print("\nОставленные строки (с минимальным AUC):")
        print(auc_df[auc_df['ModelID'].isin(duplicates['ModelID'])].sort_values('ModelID'))

    # Объединяем данные
    merged_df = auc_df.merge(mapping_df, on="ModelID", how="left")
    merged_df = merged_df.merge(expression_df, on="ModelID", how="left")
    
    # Выбираем нужные колонки
    merged_df = merged_df[['ModelID', 'area_under_curve', 'primary_disease_renamed'] + 
                         [col for col in expression_df.columns if col != 'ModelID']]
    
    return merged_df

def compute_correlations(df, analysis_type="default"):
    """Вычисление корреляций с фильтрацией по количеству точек (>=10)"""
    results = []
    genes = [col for col in df.columns if col not in ['ModelID', 'area_under_curve', 'primary_disease_renamed']]
    
    for gene in genes:
        valid_data = df[[gene, "area_under_curve"]].dropna()
        n_points = len(valid_data)
        
        # Инициализация результатов как None
        spear_corr = spear_p = pearson_corr = pearson_p = None
        skip_reason = None
        
        if n_points >= 10:
            gene_values = valid_data[gene]
            auc_values = valid_data["area_under_curve"]
            
            if gene_values.nunique() == 1:
                skip_reason = f"постоянные значения экспрессии (n_points={n_points})"
            elif auc_values.nunique() == 1:
                skip_reason = f"постоянные значения AUC (n_points={n_points})"
            else:
                try:
                    spear_corr, spear_p = spearmanr(gene_values, auc_values)
                    pearson_corr, pearson_p = pearsonr(gene_values, auc_values)
                except Exception as e:
                    skip_reason = f"ошибка расчета: {str(e)}"
        else:
            skip_reason = f"недостаточно точек ({n_points} < 10)"
        
        if skip_reason:
            print(f"Пропуск гена {gene}: {skip_reason}")
        
        results.append({
            "Gene": gene,
            "N_points": n_points,
            "Spearman_Correlation": spear_corr,
            "Spearman_P_value": spear_p,
            "Pearson_Correlation": pearson_corr,
            "Pearson_P_value": pearson_p,
            "Skip_Reason": skip_reason if skip_reason else ""
        })
    
    result_df = pd.DataFrame(results)
    
    # Рассчитываем p-adj только для существующих p-value
    for method in ['Spearman', 'Pearson']:
        valid_idx = result_df[f'{method}_P_value'].notna()
        if valid_idx.any():
            _, p_adj, _, _ = multipletests(
                result_df.loc[valid_idx, f'{method}_P_value'], 
                method='fdr_bh'
            )
            result_df.loc[valid_idx, f'{method}_P_adj'] = p_adj
        else:
            result_df[f'{method}_P_adj'] = None
    
    return result_df[[
        'Gene', 'N_points',
        'Spearman_Correlation', 'Spearman_P_value', 'Spearman_P_adj',
        'Pearson_Correlation', 'Pearson_P_value', 'Pearson_P_adj',
        'Skip_Reason'
    ]]

def save_literature_genes(df, base_path, cancer_type=None):
    """Сохранение результатов для литературных генов с дополнительным столбцом"""
    filtered_df = df[df["Gene"].isin(LITERATURE_GENES)].copy()
    if not filtered_df.empty:
        col_name = f"Expression vs Bosutinib AUC for {cancer_type}" if cancer_type else "Expression vs Bosutinib AUC for all cell lines"
        filtered_df[col_name] = ""
        filtered_df.to_csv(base_path.replace(".csv", "_literature_genes.csv"), index=False)

def analyze_cancer_types(merged_df):
    """Анализ по типам рака"""
    cancer_types = [
        'AML', 'CML', 'CLL', 'ALL', 'Lung Cancer', 
        'Neuroblastoma', 'Colon/Colorectal Cancer', 'Ovarian Cancer'
    ]
    
    for cancer in cancer_types:
        subset = merged_df[merged_df["primary_disease_renamed"] == cancer]
        if not subset.empty:
            result_df = compute_correlations(subset)
            output_file = f"{output_folder}/bosutinib_expression_{cancer.replace('/', '_').replace(' ', '_').lower()}.csv"
            
            # Добавляем столбец с названием типа рака
            result_df[f"Expression vs Bosutinib AUC for {cancer}"] = ""
            result_df.to_csv(output_file, index=False)
            save_literature_genes(result_df, output_file, cancer)
            print(f"Сохранено: {output_file}")

    # Комбинированный анализ для всех типов рака
    subset_all = merged_df[merged_df["primary_disease_renamed"].isin(cancer_types)]
    if not subset_all.empty:
        result_df = compute_correlations(subset_all)
        output_file = f"{output_folder}/bosutinib_expression_combined.csv"
        result_df["Expression vs Bosutinib AUC for combined cancer types"] = ""
        result_df.to_csv(output_file, index=False)
        save_literature_genes(result_df, output_file, "combined cancer types")
        print(f"Сохранено: {output_file}")

def analyze_all_cell_lines(merged_df):
    """Анализ для всех клеточных линий"""
    result_df = compute_correlations(merged_df)
    output_file = f"{output_folder}/bosutinib_expression_full_cell_lines.csv"
    
    # Определяем название для столбца
    cancer_types = merged_df['primary_disease_renamed'].unique()
    col_name = f"Expression vs Bosutinib AUC for {cancer_types[0]}" if len(cancer_types) == 1 else "Expression vs Bosutinib AUC for all cell lines"
    
    result_df[col_name] = ""
    result_df.to_csv(output_file, index=False)
    save_literature_genes(result_df, output_file, cancer_types[0] if len(cancer_types) == 1 else None)
    print(f"Сохранено: {output_file}")

def main():
    merged_df = load_and_prepare_data()
    analyze_cancer_types(merged_df)
    analyze_all_cell_lines(merged_df)

if __name__ == "__main__":
    main()

Обнаружены дубликаты DepMap ID:

Дубликаты для ModelID: ACH-000219
     experiment_id     ModelID  area_under_curve  master_ccl_id ccl_name
40              44  ACH-000219            11.588             30     A375
379            421  ACH-000219            12.466             30     A375

Дубликаты для ModelID: ACH-000222
     experiment_id     ModelID  area_under_curve  master_ccl_id ccl_name
662            733  ACH-000222            11.157             52    ASPC1
565            629  ACH-000222            11.635             52    ASPC1

Дубликаты для ModelID: ACH-000329
     experiment_id     ModelID  area_under_curve  master_ccl_id  ccl_name
432            483  ACH-000329            13.234            131  CCFSTTG1
446            497  ACH-000329            13.337            131  CCFSTTG1

Дубликаты для ModelID: ACH-000463
     experiment_id     ModelID  area_under_curve  master_ccl_id ccl_name
168            179  ACH-000463            12.862         128001  NCIH460
316            352  AC

In [2]:
import pandas as pd
from scipy.stats import spearmanr, pearsonr
from statsmodels.stats.multitest import multipletests

# Пути к файлам
auc_file = r"../../depmap_datasets/prepared_datasets/auc_bosutinib_ctd2.csv"
mapping_file = r"../../depmap_datasets/prepared_datasets/cancer_cell_lines_merged_data.csv"
dep_score_file = r"../../depmap_datasets/prepared_datasets/depscores.csv"
output_folder = r"./correlation_bosutinib_auc_vs_depscore"

# Гены для фильтрации
LITERATURE_GENES = [
    "ABL1", "ABL2", "AXL", "BMX", "BTK", "CAMK1D", "CAMK2G", 
    "CAV1", "CSK", "EGFR", "EPHB4", "FER", "FES", "FGR", "FRK", "FYN", 
    "HCK", "LCK", "LYN", "MAP4K2", "MAP4K5", "MINK1", "PTK2", 
    "PTK2B", "SIK1", "SIK2", "SIK3", "SRC", "STK10", "STK24", "STK4", 
    "SYK", "TBK1", "TEC", "TNK2", "YES1"
]

def load_and_prepare_data():
    """Загрузка и подготовка данных с удалением дубликатов DepMap ID"""
    # Загружаем файлы
    auc_df = pd.read_csv(auc_file)
    mapping_df = pd.read_csv(mapping_file)
    dep_score_df = pd.read_csv(dep_score_file)

    # Удаление дубликатов DepMap ID (оставляем строку с минимальным AUC)
    duplicates = auc_df[auc_df.duplicated('ModelID', keep=False)]
    if not duplicates.empty:
        print("Обнаружены дубликаты DepMap ID:")
        
        # Группируем по ModelID и выводим все дубликаты
        for model_id, group in duplicates.groupby('ModelID'):
            print(f"\nДубликаты для ModelID: {model_id}")
            print(group.sort_values('area_under_curve'))
        
        # Оставляем только строки с минимальным AUC для каждого ModelID
        auc_df = auc_df.loc[auc_df.groupby('ModelID')['area_under_curve'].idxmin()]
        
        print("\nОставленные строки (с минимальным AUC):")
        print(auc_df[auc_df['ModelID'].isin(duplicates['ModelID'])].sort_values('ModelID'))

    # Переименовываем 'DepMap_ID' в 'ModelID' для корректного объединения
    dep_score_df.rename(columns={"DepMap_ID": "ModelID"}, inplace=True)

    # Объединяем данные
    merged_df = auc_df.merge(mapping_df, on="ModelID", how="left")
    merged_df = merged_df.merge(dep_score_df, on="ModelID", how="left")
    
    # Выбираем нужные колонки
    merged_df = merged_df[['ModelID', 'area_under_curve', 'primary_disease_renamed'] + 
                         [col for col in dep_score_df.columns if col != 'ModelID']]
    
    return merged_df

def compute_correlations(df, analysis_type="default"):
    """Вычисление корреляций с фильтрацией по количеству точек (>=10)"""
    results = []
    genes = [col for col in df.columns if col not in ['ModelID', 'area_under_curve', 'primary_disease_renamed']]
    
    for gene in genes:
        valid_data = df[[gene, "area_under_curve"]].dropna()
        n_points = len(valid_data)
        
        # Инициализация результатов как None
        spear_corr = spear_p = pearson_corr = pearson_p = None
        skip_reason = None
        
        if n_points >= 10:
            gene_values = valid_data[gene]
            auc_values = valid_data["area_under_curve"]
            
            if gene_values.nunique() == 1:
                skip_reason = f"постоянные значения DepScore (n_points={n_points})"
            elif auc_values.nunique() == 1:
                skip_reason = f"постоянные значения AUC (n_points={n_points})"
            else:
                try:
                    spear_corr, spear_p = spearmanr(gene_values, auc_values)
                    pearson_corr, pearson_p = pearsonr(gene_values, auc_values)
                except Exception as e:
                    skip_reason = f"ошибка расчета: {str(e)}"
        else:
            skip_reason = f"недостаточно точек ({n_points} < 10)"
        
        if skip_reason:
            print(f"Пропуск гена {gene}: {skip_reason}")
        
        results.append({
            "Gene": gene,
            "N_points": n_points,
            "Spearman_Correlation": spear_corr,
            "Spearman_P_value": spear_p,
            "Pearson_Correlation": pearson_corr,
            "Pearson_P_value": pearson_p,
            "Skip_Reason": skip_reason if skip_reason else ""
        })
    
    result_df = pd.DataFrame(results)
    
    # Рассчитываем p-adj только для существующих p-value
    for method in ['Spearman', 'Pearson']:
        valid_idx = result_df[f'{method}_P_value'].notna()
        if valid_idx.any():
            _, p_adj, _, _ = multipletests(
                result_df.loc[valid_idx, f'{method}_P_value'], 
                method='fdr_bh'
            )
            result_df.loc[valid_idx, f'{method}_P_adj'] = p_adj
        else:
            result_df[f'{method}_P_adj'] = None
    
    return result_df[[
        'Gene', 'N_points',
        'Spearman_Correlation', 'Spearman_P_value', 'Spearman_P_adj',
        'Pearson_Correlation', 'Pearson_P_value', 'Pearson_P_adj',
        'Skip_Reason'
    ]]

def save_literature_genes(df, base_path, cancer_type=None):
    """Сохранение результатов для литературных генов с дополнительным столбцом"""
    filtered_df = df[df["Gene"].isin(LITERATURE_GENES)].copy()
    if not filtered_df.empty:
        col_name = f"Depscore vs Bosutinib AUC for {cancer_type}" if cancer_type else "Depscore vs Bosutinib AUC for all cell lines"
        filtered_df[col_name] = ""
        filtered_df.to_csv(base_path.replace(".csv", "_literature_genes.csv"), index=False)

def analyze_cancer_types(merged_df):
    """Анализ по типам рака"""
    cancer_types = [
        'AML', 'CML', 'CLL', 'ALL', 'Lung Cancer', 
        'Neuroblastoma', 'Colon/Colorectal Cancer', 'Ovarian Cancer'
    ]
    
    for cancer in cancer_types:
        subset = merged_df[merged_df["primary_disease_renamed"] == cancer]
        if not subset.empty:
            result_df = compute_correlations(subset)
            output_file = f"{output_folder}/bosutinib_depscore_{cancer.replace('/', '_').replace(' ', '_').lower().lower()}.csv"
            
            # Добавляем столбец с названием типа рака
            result_df[f"Depscore vs Bosutinib AUC for {cancer}"] = ""
            result_df.to_csv(output_file, index=False)
            save_literature_genes(result_df, output_file, cancer)
            print(f"Сохранено: {output_file}")

    # Комбинированный анализ для всех типов рака
    subset_all = merged_df[merged_df["primary_disease_renamed"].isin(cancer_types)]
    if not subset_all.empty:
        result_df = compute_correlations(subset_all)
        output_file = f"{output_folder}/bosutinib_depscore_combined.csv"
        result_df["Depscore vs Bosutinib AUC for combined cancer types"] = ""
        result_df.to_csv(output_file, index=False)
        save_literature_genes(result_df, output_file, "combined cancer types")
        print(f"Сохранено: {output_file}")

def analyze_all_cell_lines(merged_df):
    """Анализ для всех клеточных линий"""
    result_df = compute_correlations(merged_df)
    output_file = f"{output_folder}/bosutinib_depscore_full_cell_lines.csv"
    
    # Определяем название для столбца
    cancer_types = merged_df['primary_disease_renamed'].unique()
    col_name = f"Depscore vs Bosutinib AUC for {cancer_types[0]}" if len(cancer_types) == 1 else "Depscore vs Bosutinib AUC for all cell lines"
    
    result_df[col_name] = ""
    result_df.to_csv(output_file, index=False)
    save_literature_genes(result_df, output_file, cancer_types[0] if len(cancer_types) == 1 else None)
    print(f"Сохранено: {output_file}")

def main():
    merged_df = load_and_prepare_data()
    analyze_cancer_types(merged_df)
    analyze_all_cell_lines(merged_df)

if __name__ == "__main__":
    main()

Обнаружены дубликаты DepMap ID:

Дубликаты для ModelID: ACH-000219
     experiment_id     ModelID  area_under_curve  master_ccl_id ccl_name
40              44  ACH-000219            11.588             30     A375
379            421  ACH-000219            12.466             30     A375

Дубликаты для ModelID: ACH-000222
     experiment_id     ModelID  area_under_curve  master_ccl_id ccl_name
662            733  ACH-000222            11.157             52    ASPC1
565            629  ACH-000222            11.635             52    ASPC1

Дубликаты для ModelID: ACH-000329
     experiment_id     ModelID  area_under_curve  master_ccl_id  ccl_name
432            483  ACH-000329            13.234            131  CCFSTTG1
446            497  ACH-000329            13.337            131  CCFSTTG1

Дубликаты для ModelID: ACH-000463
     experiment_id     ModelID  area_under_curve  master_ccl_id ccl_name
168            179  ACH-000463            12.862         128001  NCIH460
316            352  AC

In [3]:
import pandas as pd
from scipy.stats import spearmanr, pearsonr
from statsmodels.stats.multitest import multipletests

# Пути к файлам
lfc_file = r"../../depmap_datasets/prepared_datasets/lfc_pim-447_prism.csv"
mapping_file = r"../../depmap_datasets/prepared_datasets/cancer_cell_lines_merged_data.csv"
expression_file = r"../../depmap_datasets/prepared_datasets/protein_coding_gene_expression.csv"
output_folder = r"./correlation_pim-447_lfc_vs_expression"

# Гены для фильтрации
LITERATURE_GENES = [
    "ABL1", "ABL2", "AXL", "BMX", "BTK", "CAMK1D", "CAMK2G", 
    "CAV1", "CSK", "EGFR", "EPHB4", "FER", "FES", "FGR", "FRK", "FYN", 
    "HCK", "LCK", "LYN", "MAP4K2", "MAP4K5", "MINK1", "PTK2", 
    "PTK2B", "SIK1", "SIK2", "SIK3", "SRC", "STK10", "STK24", "STK4", 
    "SYK", "TBK1", "TEC", "TNK2", "YES1"
]

def load_and_prepare_data():
    """Загрузка и подготовка данных с удалением дубликатов DepMap ID"""
    lfc_df = pd.read_csv(lfc_file)
    mapping_df = pd.read_csv(mapping_file)
    expression_df = pd.read_csv(expression_file)

    # Удаление дубликатов DepMap ID (оставляем строку с минимальным LFC)
    duplicates = lfc_df[lfc_df.duplicated('ModelID', keep=False)]
    if not duplicates.empty:
        print("Обнаружены дубликаты DepMap ID:")
        
        # Выводим все дубликаты сгруппированные по ModelID
        print("\nВсе дубликаты (сгруппированные по ModelID и отсортированные по LFC):")
        print(duplicates.sort_values(['ModelID', 'LFC']))
        
        # Оставляем только строки с минимальным LFC для каждого ModelID
        lfc_df = lfc_df.loc[lfc_df.groupby('ModelID')['LFC'].idxmin()]
        
        # Выводим оставленные строки (с минимальным LFC)
        print("\nОставленные строки (с минимальным LFC):")
        print(lfc_df[lfc_df['ModelID'].isin(duplicates['ModelID'])].sort_values('ModelID'))

    # Объединяем данные
    merged_df = lfc_df.merge(mapping_df, on="ModelID", how="left")
    merged_df = merged_df.merge(expression_df, on="ModelID", how="left")
    
    # Выбираем нужные колонки
    merged_df = merged_df[['ModelID', 'LFC', 'primary_disease_renamed'] + 
                         [col for col in expression_df.columns if col != 'ModelID']]
    
    return merged_df

def compute_correlations(df, analysis_type="default"):
    """Вычисление корреляций с фильтрацией по количеству точек (>=10)"""
    results = []
    genes = [col for col in df.columns if col not in ['ModelID', 'LFC', 'primary_disease_renamed']]
    
    for gene in genes:
        valid_data = df[[gene, "LFC"]].dropna()
        n_points = len(valid_data)
        
        # Инициализация результатов как None
        spear_corr = spear_p = pearson_corr = pearson_p = None
        skip_reason = None
        
        if n_points >= 10:
            gene_values = valid_data[gene]
            lfc_values = valid_data["LFC"]
            
            if gene_values.nunique() == 1:
                skip_reason = f"постоянные значения экспрессии (n_points={n_points})"
            elif lfc_values.nunique() == 1:
                skip_reason = f"постоянные значения LFC (n_points={n_points})"
            else:
                try:
                    spear_corr, spear_p = spearmanr(gene_values, lfc_values)
                    pearson_corr, pearson_p = pearsonr(gene_values, lfc_values)
                except Exception as e:
                    skip_reason = f"ошибка расчета: {str(e)}"
        else:
            skip_reason = f"недостаточно точек ({n_points} < 10)"
        
        if skip_reason:
            print(f"Пропуск гена {gene}: {skip_reason}")
        
        results.append({
            "Gene": gene,
            "N_points": n_points,
            "Spearman_Correlation": spear_corr,
            "Spearman_P_value": spear_p,
            "Pearson_Correlation": pearson_corr,
            "Pearson_P_value": pearson_p,
            "Skip_Reason": skip_reason if skip_reason else ""
        })
    
    result_df = pd.DataFrame(results)
    
    # Рассчитываем p-adj только для существующих p-value
    for method in ['Spearman', 'Pearson']:
        valid_idx = result_df[f'{method}_P_value'].notna()
        if valid_idx.any():
            _, p_adj, _, _ = multipletests(
                result_df.loc[valid_idx, f'{method}_P_value'], 
                method='fdr_bh'
            )
            result_df.loc[valid_idx, f'{method}_P_adj'] = p_adj
        else:
            result_df[f'{method}_P_adj'] = None
    
    return result_df[[
        'Gene', 'N_points',
        'Spearman_Correlation', 'Spearman_P_value', 'Spearman_P_adj',
        'Pearson_Correlation', 'Pearson_P_value', 'Pearson_P_adj',
        'Skip_Reason'
    ]]

def save_literature_genes(df, base_path, cancer_type=None):
    """Сохранение результатов для литературных генов с дополнительным столбцом"""
    filtered_df = df[df["Gene"].isin(LITERATURE_GENES)].copy()
    if not filtered_df.empty:
        col_name = f"Expression vs PIM-447 LFC for {cancer_type}" if cancer_type else "Expression vs PIM-447 LFC for all cell lines"
        filtered_df[col_name] = ""
        filtered_df.to_csv(base_path.replace(".csv", "_literature_genes.csv"), index=False)

def analyze_cancer_types(merged_df):
    """Анализ по типам рака"""
    cancer_types = [
        'AML', 'CML', 'CLL', 'ALL', 'Lung Cancer', 
        'Neuroblastoma', 'Colon/Colorectal Cancer', 'Ovarian Cancer'
    ]
    
    for cancer in cancer_types:
        subset = merged_df[merged_df["primary_disease_renamed"] == cancer]
        if not subset.empty:
            result_df = compute_correlations(subset)
            output_file = f"{output_folder}/pim-447_expression_{cancer.replace('/', '_').replace(' ', '_').lower().lower()}.csv"
            
            # Добавляем столбец с названием типа рака
            result_df[f"Expression vs PIM-447 LFC for {cancer}"] = ""
            result_df.to_csv(output_file, index=False)
            save_literature_genes(result_df, output_file, cancer)
            print(f"Сохранено: {output_file}")

    # Комбинированный анализ для всех типов рака
    subset_all = merged_df[merged_df["primary_disease_renamed"].isin(cancer_types)]
    if not subset_all.empty:
        result_df = compute_correlations(subset_all)
        output_file = f"{output_folder}/pim-447_expression_combined.csv"
        result_df["Expression vs PIM-447 LFC for combined cancer types"] = ""
        result_df.to_csv(output_file, index=False)
        save_literature_genes(result_df, output_file, "combined cancer types")
        print(f"Сохранено: {output_file}")

def analyze_all_cell_lines(merged_df):
    """Анализ для всех клеточных линий"""
    result_df = compute_correlations(merged_df)
    output_file = f"{output_folder}/pim-447_expression_full_cell_lines.csv"
    
    # Определяем название для столбца
    cancer_types = merged_df['primary_disease_renamed'].unique()
    col_name = f"Expression vs PIM-447 LFC for {cancer_types[0]}" if len(cancer_types) == 1 else "Expression vs PIM-447 LFC for all cell lines"
    
    result_df[col_name] = ""
    result_df.to_csv(output_file, index=False)
    save_literature_genes(result_df, output_file, cancer_types[0] if len(cancer_types) == 1 else None)
    print(f"Сохранено: {output_file}")

def main():
    merged_df = load_and_prepare_data()
    analyze_cancer_types(merged_df)
    analyze_all_cell_lines(merged_df)

if __name__ == "__main__":
    main()

Сохранено: ./correlation_pim-447_lfc_vs_expression/pim-447_expression_aml.csv
Пропуск гена DAZ3: постоянные значения экспрессии (n_points=11)
Пропуск гена OR8J3: постоянные значения экспрессии (n_points=11)
Пропуск гена KRTAP13-2: постоянные значения экспрессии (n_points=11)
Пропуск гена KRTAP19-8: постоянные значения экспрессии (n_points=11)
Пропуск гена SPPL2C: постоянные значения экспрессии (n_points=11)
Пропуск гена C16orf78: постоянные значения экспрессии (n_points=11)
Пропуск гена PRAMEF8: постоянные значения экспрессии (n_points=11)
Пропуск гена MBD3L3: постоянные значения экспрессии (n_points=11)
Пропуск гена KRTAP11-1: постоянные значения экспрессии (n_points=11)
Пропуск гена OR4D2: постоянные значения экспрессии (n_points=11)
Пропуск гена FGF3: постоянные значения экспрессии (n_points=11)
Пропуск гена RNASE9: постоянные значения экспрессии (n_points=11)
Пропуск гена KRT32: постоянные значения экспрессии (n_points=11)
Пропуск гена IFNA17: постоянные значения экспрессии (n_poin

In [4]:
import pandas as pd
from scipy.stats import spearmanr, pearsonr
from statsmodels.stats.multitest import multipletests

# Пути к файлам
lfc_file = r"../../depmap_datasets/prepared_datasets/lfc_pim-447_prism.csv"
mapping_file = r"../../depmap_datasets/prepared_datasets/cancer_cell_lines_merged_data.csv"
dep_score_file = r"../../depmap_datasets/prepared_datasets/depscores.csv"
output_folder = r"./correlation_pim-447_lfc_vs_depscore"

# Гены для фильтрации
LITERATURE_GENES = [
    "ABL1", "ABL2", "AXL", "BMX", "BTK", "CAMK1D", "CAMK2G", 
    "CAV1", "CSK", "EGFR", "EPHB4", "FER", "FES", "FGR", "FRK", "FYN", 
    "HCK", "LCK", "LYN", "MAP4K2", "MAP4K5", "MINK1", "PTK2", 
    "PTK2B", "SIK1", "SIK2", "SIK3", "SRC", "STK10", "STK24", "STK4", 
    "SYK", "TBK1", "TEC", "TNK2", "YES1"
]

def load_and_prepare_data():
    """Загрузка и подготовка данных с удалением дубликатов DepMap ID"""
    lfc_df = pd.read_csv(lfc_file)
    mapping_df = pd.read_csv(mapping_file)
    dep_score_df = pd.read_csv(dep_score_file)
    
    # Переименовываем 'DepMap_ID' в 'ModelID' для корректного объединения
    dep_score_df.rename(columns={"DepMap_ID": "ModelID"}, inplace=True)

    # Удаление дубликатов DepMap ID (оставляем строку с минимальным LFC)
    duplicates = lfc_df[lfc_df.duplicated('ModelID', keep=False)]
    if not duplicates.empty:
        print("Обнаружены дубликаты DepMap ID:")
        
        # Выводим все дубликаты сгруппированные по ModelID
        print("\nВсе дубликаты (сгруппированные по ModelID и отсортированные по LFC):")
        print(duplicates.sort_values(['ModelID', 'LFC']))
        
        # Оставляем только строки с минимальным LFC для каждого ModelID
        lfc_df = lfc_df.loc[lfc_df.groupby('ModelID')['LFC'].idxmin()]
        
        # Выводим оставленные строки (с минимальным LFC)
        print("\nОставленные строки (с минимальным LFC):")
        print(lfc_df[lfc_df['ModelID'].isin(duplicates['ModelID'])].sort_values('ModelID'))

    # Объединяем данные
    merged_df = lfc_df.merge(mapping_df, on="ModelID", how="left")
    merged_df = merged_df.merge(dep_score_df, on="ModelID", how="left")
    
    # Выбираем нужные колонки
    merged_df = merged_df[['ModelID', 'LFC', 'primary_disease_renamed'] + 
                       [col for col in dep_score_df.columns if col != 'ModelID']]
    
    return merged_df

def compute_correlations(df, analysis_type="default"):
    """Вычисление корреляций с фильтрацией по количеству точек (>=10)"""
    results = []
    genes = [col for col in df.columns if col not in ['ModelID', 'LFC', 'primary_disease_renamed']]
    
    for gene in genes:
        valid_data = df[[gene, "LFC"]].dropna()
        n_points = len(valid_data)
        
        # Инициализация результатов как None
        spear_corr = spear_p = pearson_corr = pearson_p = None
        skip_reason = None
        
        if n_points >= 10:
            gene_values = valid_data[gene]
            lfc_values = valid_data["LFC"]
            
            if gene_values.nunique() == 1:
                skip_reason = f"постоянные значения DepScore (n_points={n_points})"
            elif lfc_values.nunique() == 1:
                skip_reason = f"постоянные значения LFC (n_points={n_points})"
            else:
                try:
                    spear_corr, spear_p = spearmanr(gene_values, lfc_values)
                    pearson_corr, pearson_p = pearsonr(gene_values, lfc_values)
                except Exception as e:
                    skip_reason = f"ошибка расчета: {str(e)}"
        else:
            skip_reason = f"недостаточно точек ({n_points} < 10)"
        
        if skip_reason:
            print(f"Пропуск гена {gene}: {skip_reason}")
        
        results.append({
            "Gene": gene,
            "N_points": n_points,
            "Spearman_Correlation": spear_corr,
            "Spearman_P_value": spear_p,
            "Pearson_Correlation": pearson_corr,
            "Pearson_P_value": pearson_p,
            "Skip_Reason": skip_reason if skip_reason else ""
        })
    
    result_df = pd.DataFrame(results)
    
    # Рассчитываем p-adj только для существующих p-value
    for method in ['Spearman', 'Pearson']:
        valid_idx = result_df[f'{method}_P_value'].notna()
        if valid_idx.any():
            _, p_adj, _, _ = multipletests(
                result_df.loc[valid_idx, f'{method}_P_value'], 
                method='fdr_bh'
            )
            result_df.loc[valid_idx, f'{method}_P_adj'] = p_adj
        else:
            result_df[f'{method}_P_adj'] = None
    
    return result_df[[
        'Gene', 'N_points',
        'Spearman_Correlation', 'Spearman_P_value', 'Spearman_P_adj',
        'Pearson_Correlation', 'Pearson_P_value', 'Pearson_P_adj',
        'Skip_Reason'
    ]]

def save_literature_genes(df, base_path, cancer_type=None):
    """Сохранение результатов для литературных генов с дополнительным столбцом"""
    filtered_df = df[df["Gene"].isin(LITERATURE_GENES)].copy()
    if not filtered_df.empty:
        col_name = f"Depscore vs PIM-447 LFC for {cancer_type}" if cancer_type else "Depscore vs PIM-447 LFC for all cell lines"
        filtered_df[col_name] = ""
        filtered_df.to_csv(base_path.replace(".csv", "_literature_genes.csv"), index=False)

def analyze_cancer_types(merged_df):
    """Анализ по типам рака"""
    cancer_types = [
        'AML', 'CML', 'CLL', 'ALL', 'Lung Cancer', 
        'Neuroblastoma', 'Colon/Colorectal Cancer', 'Ovarian Cancer'
    ]
    
    for cancer in cancer_types:
        subset = merged_df[merged_df["primary_disease_renamed"] == cancer]
        if not subset.empty:
            result_df = compute_correlations(subset)
            output_file = f"{output_folder}/pim-447_depscores_{cancer.replace('/', '_').replace(' ', '_').lower().lower()}.csv"
            
            # Добавляем столбец с названием типа рака
            result_df[f"Depscore vs PIM-447 LFC for {cancer}"] = ""
            result_df.to_csv(output_file, index=False)
            save_literature_genes(result_df, output_file, cancer)
            print(f"Сохранено: {output_file}")

    # Комбинированный анализ для всех типов рака
    subset_all = merged_df[merged_df["primary_disease_renamed"].isin(cancer_types)]
    if not subset_all.empty:
        result_df = compute_correlations(subset_all)
        output_file = f"{output_folder}/pim-447_depscores_combined.csv"
        result_df["Depscore vs PIM-447 LFC for combined cancer types"] = ""
        result_df.to_csv(output_file, index=False)
        save_literature_genes(result_df, output_file, "combined cancer types")
        print(f"Сохранено: {output_file}")

def analyze_all_cell_lines(merged_df):
    """Анализ для всех клеточных линий"""
    result_df = compute_correlations(merged_df)
    output_file = f"{output_folder}/pim-447_depscores_full_cell_lines.csv"
    
    # Определяем название для столбца
    cancer_types = merged_df['primary_disease_renamed'].unique()
    col_name = f"Depscore vs PIM-447 LFC for {cancer_types[0]}" if len(cancer_types) == 1 else "Depscore vs PIM-447 LFC for all cell lines"
    
    result_df[col_name] = ""
    result_df.to_csv(output_file, index=False)
    save_literature_genes(result_df, output_file, cancer_types[0] if len(cancer_types) == 1 else None)
    print(f"Сохранено: {output_file}")

def main():
    merged_df = load_and_prepare_data()
    analyze_cancer_types(merged_df)
    analyze_all_cell_lines(merged_df)

if __name__ == "__main__":
    main()

Пропуск гена AAED1: недостаточно точек (2 < 10)
Пропуск гена ABCA11P: недостаточно точек (7 < 10)
Пропуск гена ABCC6P1: недостаточно точек (6 < 10)
Пропуск гена ACOXL-AS1: недостаточно точек (2 < 10)
Пропуск гена ACTG1P20: недостаточно точек (6 < 10)
Пропуск гена ACTG1P4: недостаточно точек (6 < 10)
Пропуск гена ACTR3BP5&ACTR3BP2: недостаточно точек (2 < 10)
Пропуск гена AHSA2: недостаточно точек (2 < 10)
Пропуск гена AKAP2: недостаточно точек (2 < 10)
Пропуск гена ALMS1P1: недостаточно точек (2 < 10)
Пропуск гена ALS2CR12: недостаточно точек (2 < 10)
Пропуск гена AMELY: недостаточно точек (2 < 10)
Пропуск гена AMZ2P1: недостаточно точек (7 < 10)
Пропуск гена ANKRD18B: недостаточно точек (6 < 10)
Пропуск гена ANKRD18DP: недостаточно точек (2 < 10)
Пропуск гена ANKRD19P: недостаточно точек (2 < 10)
Пропуск гена ANKRD20A11P: недостаточно точек (2 < 10)
Пропуск гена ANKRD20A19P: недостаточно точек (7 < 10)
Пропуск гена ANKRD20A2&ANKRD20A1: недостаточно точек (7 < 10)
Пропуск гена ANKRD20A